# Dan's code for animation

In [1]:
%matplotlib notebook

#every line of code in the first 4 boxes is from mirs covid_plot unless stated otherwise 
import matplotlib.pyplot as plt
import pandas as pd
import numpy as np
import scipy.stats as st
from scipy.stats import linregress
import gmaps
from ipywidgets.embed import embed_minimal_html
import seaborn as sns
import plotly.express as px
import re
import gmaps.geojson_geometries
from matplotlib.cm import viridis
from matplotlib.cm import Spectral
from matplotlib.colors import to_hex
import country_converter as coco
import os

#this will be will be the stuff ill be using on the animated graphs. im adding them as i see a tutorial
#Not necessarilly deteling them like those on top. In which I can guarantee i am not using half of those.
#I will only cite the ones that ends up working
import matplotlib as cm
import matplotlib.pyplot as plt
import matplotlib.animation as animation
import pandas_alive
from celluloid import Camera
from matplotlib.animation import FuncAnimation
import plotly.express as px
import plotly.io as pio
from IPython.display import HTML
from tqdm import tqdm


#this is the only i used. I am not deleting the ones on top because it shows what i did to get to this point
import bar_chart_race as bcr

In [2]:
# covid_stats_df =  pd.read_csv("Output/covid_stats_2020.csv")
# covid_stats_df.head()



In [3]:
ultimate_no_null_df = pd.read_csv("Output/ultimate_no_null.csv")
ultimate_no_null_df.head(-1)
ultimate_no_null_df['Infection_rate'] = ultimate_no_null_df['Infection_rate'].str.rstrip('%').astype('float')




In [4]:

# ultimate_no_null_df['month'] = ultimate_no_null_df['month'].astype('str')
# modifiednull = ultimate_no_null_df["month"].replace({"1": "1January", "2": "2February",
#                                                     "3": "3March", "4": " 4April",
#                                                     "5": "5May", "6": " 6June",
#                                                     "7": "7July", "8": "8August",
#                                                     "9": "9September", "10": "10October",
#                                                     "11": "11November", "12": "12December"}, inplace=True)


#I wanted to replace the month number to the months, but since the months would become an index, i notice that no matter what
#i did it would alphabeticize the months. Destroying the point of the whole thing. So wwe are force to use months number instead 
#of having their actual names. Uncomment this portion out if you want to see it.

In [5]:
ConfirmedDESC = ultimate_no_null_df.sort_values(by=['Confirmed'], ascending = True).reset_index()
ConfirmedDESC.head(10)

#i will need these to copy and paste the correct file names
#sorting the other data fram. Puprposely not removing the population on this one. Will  do so later if this works
#This should be obvious since this is the beginning. This is not really relevant. Unless its group by countries

index standard_names  month  year  Confirmed  stringency_index        lat  \
0      0    Afghanistan      1  2020        0.0          0.000000  33.939110   
1   1212        Morocco      1  2020        0.0          0.000000  31.791702   
2    595        Estonia      1  2020        0.0          0.000000  58.595272   
3    587        Eritrea      5  2020        0.0         93.520000  15.179384   
4    584        Eritrea      2  2020        0.0          0.000000  15.179384   
5    583        Eritrea      1  2020        0.0          0.000000  15.179384   
6   1666          Spain      1  2020        0.0          0.358387  40.463667   
7    572    El Salvador      2  2020        0.0         19.440000  13.794185   
8    571    El Salvador      1  2020        0.0          3.494194  13.794185   
9   1679      Sri Lanka      2  2020        0.0          8.905172   7.873054   

         lng  Population (2020)  Density (P/Km²)  Infection_rate ISO_2 ISO_3  \
0  67.709953           39074280               60             0.0    AF   AFG   
1  -7.092620           36985624               83             0.0    MA   MAR   
2  25.013607            1326693               31             0.0    EE   EST   
3  39.782334            3554797               35             0.0    ER   ERI   
4  39.782334            3554797               35             0.0    ER   ERI   
5  39.782334            3554797               35             0.0    ER   ERI   
6  -3.749220           46757980               94             0.0    ES   ESP   
7 -88.896530            6491923              313             0.0    SV   SLV   
8 -88.896530            6491923              313             0.0    SV   SLV   
9  80.771797           21428970              341             0.0    LK   LKA   

   Infection_rate_f  
0               0.0  
1               0.0  
2               0.0  
3               0.0  
4               0.0  
5               0.0  
6               0.0  
7               0.0  
8               0.0  
9               0.0

In [6]:
#Race Bar Chart
Pivot = ultimate_no_null_df.pivot(index='month', columns='standard_names', values='Infection_rate')
Pivot



#its very important to not reset index in this particular chart because if we reset the index month will be treated as a standard name

#I was going to remove the NAN values but the NAN values shows that the countries are not reporting their values for that month.
    #And i was not interested in turn NAN to 0 because that would be giving false data.
    



#In order for the racing bar chart to work, we need first to make turn our df into a wide format.
#So that the month can be the new index, the countries are the new columns, and for this first one will be using the infectionr rate values,
    #The later charts will be using different value, and that will be the only change

#source = https://chrisalbon.com/python/data_wrangling/pandas_long_to_wide/


#changing the data to wide.
# With month as the Index, the countries as the columns, and the Confirmed Cases as the values

standard_names  Afghanistan  Albania  Algeria  Andorra  Angola  Argentina  \
month                                                                       
1                    0.0000   0.0000   0.0000   0.0000  0.0000     0.0000   
2                    0.0000   0.0000   0.0000   0.0000  0.0000     0.0000   
3                    0.0004   0.0084   0.0016   0.4865  0.0000     0.0023   
4                    0.0050   0.0184   0.0075   0.4774  0.0001     0.0075   
5                    0.0335   0.0127   0.0122   0.0246  0.0002     0.0274   
6                    0.0417   0.0486   0.0103   0.1177  0.0006     0.1053   
7                    0.0132   0.0953   0.0375   0.0906  0.0026     0.2801   
8                    0.0038   0.1473   0.0321   0.3248  0.0046     0.5002   
9                    0.0028   0.1437   0.0160   1.1308  0.0070     0.7362   
10                   0.0055   0.2511   0.0146   3.5012  0.0177     0.9188   
11                   0.0124   0.6015   0.0574   2.5735  0.0131     0.5691   
12                      NaN   0.4804   0.0254   1.0015  0.0043     0.2360   

standard_names  Australia  Austria  Azerbaijan  Bahrain  ...  United Kingdom  \
month                                                    ...                   
1                  0.0000   0.0000      0.0000   0.0000  ...          0.0000   
2                  0.0001   0.0001      0.0000   0.0024  ...          0.0003   
3                  0.0177   0.1128      0.0029   0.0307  ...          0.1953   
4                  0.0086   0.0585      0.0148   0.1445  ...          0.3487   
5                  0.0017   0.0142      0.0363   0.4885  ...          0.1159   
6                  0.0028   0.0115      0.1185   0.8977  ...          0.0407   
7                  0.0366   0.0373      0.1413   0.8313  ...          0.0288   
8                  0.0334   0.0700      0.0449   0.6423  ...          0.0490   
9                  0.0050   0.1927      0.0374   1.1041  ...          0.1733   
10                 0.0020   0.6668      0.1481   0.6301  ...          0.8226   
11                 0.0012   1.9692      0.6490   0.3104  ...          0.9109   
12                    NaN      NaN      0.7311   0.1711  ...          0.5138   

standard_names  United States  Uruguay  Uzbekistan  Vanuatu  Venezuela  \
month                                                                    
1                      0.0000   0.0000      0.0000   0.0000     0.0000   
2                      0.0000   0.0000      0.0000   0.0000     0.0000   
3                      0.0580   0.0097      0.0005   0.0000     0.0005   
4                      0.2668   0.0232      0.0056   0.0000     0.0007   
5                      0.2168   0.0052      0.0047   0.0000     0.0041   
6                      0.2520   0.0033      0.0145   0.0000     0.0152   
7                      0.5806   0.0094      0.0462   0.0000     0.0448   
8                      0.4418   0.0095      0.0533   0.0000     0.0991   
9                      0.3630   0.0130      0.0442   0.0000     0.0999   
10                     0.5786   0.0310      0.0304   0.0000     0.0594   
11                     1.3467   0.0786      0.0184   0.0003     0.0365   
12                     1.1649   0.1753      0.0077   0.0000     0.0246   

standard_names  Vietnam   Yemen  Zambia  Zimbabwe  
month                                              
1                0.0000  0.0000  0.0000    0.0000  
2                0.0000  0.0000  0.0000    0.0000  
3                0.0002  0.0000  0.0002    0.0001  
4                0.0001  0.0000  0.0004    0.0002  
5                0.0001  0.0011  0.0051    0.0012  
6                0.0000  0.0028  0.0029    0.0028  
7                0.0002  0.0019  0.0237    0.0173  
8                0.0005  0.0069  0.0332    0.0223  
9                0.0001  0.0003  0.0144    0.0090  
10               0.0001  0.0001  0.0091    0.0036  
11               0.0002  0.0004  0.0066    0.0106  
12               0.0001     NaN  0.0050    0.0141  

[12 rows x 170 columns]

In [7]:
#Unfortunately the infection rate(confirmed case at month/total population) is
#small that some countries will look like 0. And the moving bar chart
#will show zero

In [8]:
#source = https://www.youtube.com/watch?v=eF9VH4zKoTI
#source2 = https://github.com/dexplo/

race = bcr.bar_chart_race(Pivot, 
                   n_bars = 10,steps_per_period=28,period_length=2000,  
                   title='Top 10 Infection Rate Per Month',     
                   period_summary_func=lambda v, r: {'x': .98, 'y': .2, 's': f'Average Infection Rate: {v.mean():,.0f}', 'ha': 'right', 'size': 11}
                  )

race
#I tried changing the months in to their actual month names instead of their month number, but the because 

#wait about 3 -5 minutes

#I wants smooth animation so I made it to 30fps with each month being on 2 seconds long



C:\Users\danza\.conda\envs\PythonData\lib\site-packages\matplotlib\backends\backend_agg.py:238: RuntimeWarning: Glyph 127 missing from current font.
  font.set_text(s, 0.0, flags=flags)
C:\Users\danza\.conda\envs\PythonData\lib\site-packages\matplotlib\backends\backend_agg.py:238: RuntimeWarning: Glyph 128 missing from current font.
  font.set_text(s, 0.0, flags=flags)
C:\Users\danza\.conda\envs\PythonData\lib\site-packages\matplotlib\backends\backend_agg.py:238: RuntimeWarning: Glyph 129 missing from current font.
  font.set_text(s, 0.0, flags=flags)
C:\Users\danza\.conda\envs\PythonData\lib\site-packages\matplotlib\backends\backend_agg.py:238: RuntimeWarning: Glyph 130 missing from current font.
  font.set_text(s, 0.0, flags=flags)
C:\Users\danza\.conda\envs\PythonData\lib\site-packages\matplotlib\backends\backend_agg.py:238: RuntimeWarning: Glyph 131 missing from current font.
  font.set_text(s, 0.0, flags=flags)
C:\Users\danza\.conda\envs\PythonData\lib\site-packages\matplotlib\bac

C:\Users\danza\.conda\envs\PythonData\lib\site-packages\bar_chart_race\_make_chart.py:226: UserWarning: Some of your columns never make an appearance in the animation. To reduce color repetition, set `filter_column_colors` to `True`
  warnings.warn("Some of your columns never make an appearance in the animation. "


In [9]:
# race.save('Video/infrace.mp4', writer=writer)

In [10]:
other = ultimate_no_null_df.pivot(index='month', columns='standard_names', values='stringency_index')




other

standard_names  Afghanistan    Albania    Algeria    Andorra     Angola  \
month                                                                     
1                  0.000000   0.000000   0.000000   0.000000   0.000000   
2                  2.010690   3.545172   0.000000   0.000000   4.601379   
3                 40.831935  58.570968  37.486129  21.624839  24.400000   
4                 80.740000  86.665000  86.155333  53.179667  87.529333   
5                 84.260000  87.421613  77.566774  50.896774  78.524839   
6                 80.182667  70.466000  70.554333  42.837000  76.361667   
7                 78.700000  63.856774  72.548387  42.502258  76.450645   
8                 55.408710  58.125484  79.989032  45.370000  78.183548   
9                 23.520000  54.630000  75.930000  48.146667  78.010000   
10                16.460323  54.630000  75.630000  57.405161  69.804839   
11                 7.591333  60.309667  71.697333  62.220000  59.217000   
12                      NaN  65.740000  72.220000  59.260000  57.410000   

standard_names  Argentina  Australia    Austria  Azerbaijan    Bahrain  ...  \
month                                                                   ...   
1                3.225484   2.508710   0.000000    0.179355   3.135484  ...   
2               11.110000  19.440000   2.298621    4.120690  17.528966  ...   
3               51.702581  38.200323  52.926129   49.762258  49.195484  ...   
4               98.457000  71.480667  78.642000   89.785333  75.986667  ...   
5               90.262581  67.352258  60.601935   82.558387  75.000000  ...   
6               89.136667  55.014333  47.744667   85.743333  75.000000  ...   
7               91.515484  69.819355  38.682581   95.941290  70.516129  ...   
8               88.259355  78.213226  35.190000   87.608387  66.754516  ...   
9               87.960000  74.720000  36.637333   77.192333  61.793000  ...   
10              83.958710  64.235484  51.165484   66.769355  63.531290  ...   
11              79.631667  49.982000  78.118333   66.018000  58.330000  ...   
12              79.170000        NaN        NaN   72.133000  58.330000  ...   

standard_names  United Kingdom  United States    Uruguay  Uzbekistan  \
month                                                                  
1                     2.241613       0.000000   0.000000    3.942258   
2                    11.014138       5.368276   0.000000   11.110000   
3                    36.633226      45.774516  33.870968   46.657419   
4                    79.630000      72.690000  65.985667   91.296000   
5                    74.225161      72.690000  61.110000   89.307742   
6                    70.866000      70.711333  57.655333   72.066000   
7                    65.381290      68.263871  29.392581   69.804194   
8                    67.636129      67.130000  29.420968   61.469355   
9                    65.569333      64.197667  37.965000   44.383333   
10                   67.891290      64.051613  43.520000   41.964194   
11                   71.666333      69.628667  43.520000   39.810000   
12                   69.908125      72.044615  49.537143   39.810000   

standard_names    Vanuatu  Venezuela    Vietnam      Yemen     Zambia  \
month                                                                   
1                0.000000   0.000000   2.778387   0.000000   0.000000   
2                0.000000   0.766207  40.866897   0.000000   5.173448   
3               16.128387  52.150968  53.492903  18.458710  24.016774   
4               77.408000  82.410000  88.814000  40.586333  57.686333   
5               72.762581  84.113871  71.473548  56.957419  49.507742   
6               66.670000  81.111000  63.331000  58.330000  42.034000   
7               66.670000  86.740000  58.545806  41.873548  50.930000   
8               60.934516  85.035806  77.253548  31.480000  50.210000   
9               22.220000  82.965000  72.178333  29.322667  48.982667   
10              22.220000  86.

In [11]:
race = bcr.bar_chart_race(other, 
                   n_bars = 10,steps_per_period=30,period_length=2000,  
                   title='Top 10 Countries With Highest Controls on Covid', 
                    period_summary_func=lambda v, r: {'x': .98, 'y': .2, 's': f'Average Stringency Index: {v.mean():,.0f}', 'ha': 'right', 'size': 11}
#                    filename='animated\stringan.mp4'
                  )

race

# steps_per_period = 28. I am a video gamer so 60fps is a must for me. But since there



C:\Users\danza\.conda\envs\PythonData\lib\site-packages\matplotlib\backends\backend_agg.py:238: RuntimeWarning: Glyph 127 missing from current font.
  font.set_text(s, 0.0, flags=flags)
C:\Users\danza\.conda\envs\PythonData\lib\site-packages\matplotlib\backends\backend_agg.py:238: RuntimeWarning: Glyph 128 missing from current font.
  font.set_text(s, 0.0, flags=flags)
C:\Users\danza\.conda\envs\PythonData\lib\site-packages\matplotlib\backends\backend_agg.py:238: RuntimeWarning: Glyph 129 missing from current font.
  font.set_text(s, 0.0, flags=flags)
C:\Users\danza\.conda\envs\PythonData\lib\site-packages\matplotlib\backends\backend_agg.py:238: RuntimeWarning: Glyph 130 missing from current font.
  font.set_text(s, 0.0, flags=flags)
C:\Users\danza\.conda\envs\PythonData\lib\site-packages\matplotlib\backends\backend_agg.py:238: RuntimeWarning: Glyph 131 missing from current font.
  font.set_text(s, 0.0, flags=flags)
C:\Users\danza\.conda\envs\PythonData\lib\site-packages\matplotlib\bac

C:\Users\danza\.conda\envs\PythonData\lib\site-packages\bar_chart_race\_make_chart.py:226: UserWarning: Some of your columns never make an appearance in the animation. To reduce color repetition, set `filter_column_colors` to `True`
  warnings.warn("Some of your columns never make an appearance in the animation. "


In [12]:
cases = ultimate_no_null_df.pivot(index='month', columns='standard_names', values='Confirmed')

cases



standard_names  Afghanistan  Albania  Algeria  Andorra  Angola  Argentina  \
month                                                                       
1                       0.0      0.0      0.0      0.0     0.0        0.0   
2                       1.0      0.0      1.0      0.0     0.0        0.0   
3                     174.0    243.0    715.0    376.0     7.0     1054.0   
4                    1952.0    530.0   3290.0    369.0    20.0     3374.0   
5                   13081.0    364.0   5388.0     19.0    59.0    12423.0   
6                   16299.0   1398.0   4513.0     91.0   198.0    47679.0   
7                    5158.0   2741.0  16487.0     70.0   864.0   126772.0   
8                    1494.0   4237.0  14100.0    251.0  1506.0   226433.0   
9                    1109.0   4136.0   7036.0    874.0  2318.0   333266.0   
10                   2157.0   7226.0   6412.0   2706.0  5833.0   415923.0   
11                   4849.0  17307.0  25257.0   1989.0  4334.0   257609.0   
12                      NaN  13822.0  11172.0    774.0  1423.0   106841.0   

standard_names  Australia   Austria  Azerbaijan  Bahrain  ...  United Kingdom  \
month                                                     ...                   
1                     9.0       0.0         0.0      0.0  ...             2.0   
2                    16.0       9.0         0.0     41.0  ...           199.0   
3                  4534.0   10171.0       298.0    526.0  ...        132701.0   
4                  2207.0    5272.0      1506.0   2473.0  ...        236937.0   
5                   436.0    1279.0      3690.0   8358.0  ...         78768.0   
6                   718.0    1035.0     12030.0  15360.0  ...         27677.0   
7                  9360.0    3364.0     14354.0  14224.0  ...         19577.0   
8                  8539.0    6308.0      4557.0  10990.0  ...         33290.0   
9                  1277.0   17375.0      3794.0  18892.0  ...        117763.0   
10                  499.0   60112.0     15040.0  10781.0  ...        558947.0   
11                  317.0  177531.0     65907.0   5311.0  ...        618940.0   
12                    NaN       NaN     74246.0   2927.0  ...        349095.0   

standard_names  United States  Uruguay  Uzbekistan  Vanuatu  Venezuela  \
month                                                                    
1                         8.0      0.0         0.0      0.0        0.0   
2                        17.0      0.0         0.0      0.0        0.0   
3                    192152.0    338.0       172.0      0.0      135.0   
4                    884047.0    806.0      1867.0      0.0      198.0   
5                    718241.0    180.0      1584.0      0.0     1177.0   
6                    834974.0    113.0      4880.0      0.0     4322.0   
7                   1923898.0    328.0     15506.0      0.0    12742.0   
8                   1463760.0    331.0     17884.0      0.0    28154.0   
9                   1202896.0    451.0     14824.0      0.0    28394.0   
10                  1917201.0   1078.0     10215.0      0.0    16891.0   
11                  4462302.0   2733.0      6162.0      1.0    10381.0   
12                  3859800.0   6093.0      2581.0      0.0     7001.0   

standard_names  Vietnam   Yemen  Zambia  Zimbabwe  
month                                              
1                   2.0     0.0     0.0       0.0  
2                  14.0     0.0     0.0       0.0  
3                 196.0     0.0    35.0       8.0  
4                  58.0     6.0    71.0      32.0  
5                  58.0   317.0   951.0     178.0  
6                  27.0   835.0   537.0     413.0  
7                 203.0   570.0  4369.0    2578.0  
8                 486.0  2062.0  6134.0    3328.0  
9                  50.0    76.0  2662.0    1341.0  
10                 86.0    29.0  1673.0     529.0  
11                167.0   128.0  1215.0    1583.0  
12                 63.0     NaN   928.0    2097.0  

[12 rows x 170 colum

In [13]:
race = bcr.bar_chart_race(cases, 
                   n_bars = 10,steps_per_period=20,period_length=2000,  
                   title='Top 10 COVID COnfirmed Cases Per Month',     
                   period_summary_func=lambda v, r: {'x': .98, 'y': .2, 's': f'Total Cases: {v.sum():,.0f}', 'ha': 'right', 'size': 11}
                  )

race
#There is a summary table that adds up the all the total confirmed cases per month.

C:\Users\danza\.conda\envs\PythonData\lib\site-packages\matplotlib\backends\backend_agg.py:238: RuntimeWarning: Glyph 127 missing from current font.
  font.set_text(s, 0.0, flags=flags)
C:\Users\danza\.conda\envs\PythonData\lib\site-packages\matplotlib\backends\backend_agg.py:238: RuntimeWarning: Glyph 128 missing from current font.
  font.set_text(s, 0.0, flags=flags)
C:\Users\danza\.conda\envs\PythonData\lib\site-packages\matplotlib\backends\backend_agg.py:238: RuntimeWarning: Glyph 129 missing from current font.
  font.set_text(s, 0.0, flags=flags)
C:\Users\danza\.conda\envs\PythonData\lib\site-packages\matplotlib\backends\backend_agg.py:238: RuntimeWarning: Glyph 130 missing from current font.
  font.set_text(s, 0.0, flags=flags)
C:\Users\danza\.conda\envs\PythonData\lib\site-packages\matplotlib\backends\backend_agg.py:238: RuntimeWarning: Glyph 131 missing from current font.
  font.set_text(s, 0.0, flags=flags)
C:\Users\danza\.conda\envs\PythonData\lib\site-packages\matplotlib\bac

C:\Users\danza\.conda\envs\PythonData\lib\site-packages\bar_chart_race\_make_chart.py:226: UserWarning: Some of your columns never make an appearance in the animation. To reduce color repetition, set `filter_column_colors` to `True`
  warnings.warn("Some of your columns never make an appearance in the animation. "
